### **Training TFT model for Apple stock dataset**

#### Installing required Libraries

In [ ]:
!pip install lightning pytorch_forecasting optuna keras

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 811.0/811.0 kB 44.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 181.9/181.9 kB 14.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 364.4/364.4 kB 25.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.5/233.5 kB 18.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 926.4/926.4 kB 52.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 815.2/815.2 kB 47.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 5.8 MB/s eta 0:00:00


#### Imporing Required Libraries

In [ ]:
# General-purpose libraries
import copy
from pathlib import Path
import warnings
import numpy as np
import pandas as pd
import os
import torch
import random

# PyTorch Lightning and Forecasting
import lightning.pytorch as pl
from lightning.pytorch.callbacks import EarlyStopping, LearningRateMonitor
from lightning.pytorch.loggers import TensorBoardLogger
from pytorch_forecasting import (
    Baseline,
    TemporalFusionTransformer,
    TimeSeriesDataSet,
)
from pytorch_forecasting.data import GroupNormalizer, NaNLabelEncoder
from pytorch_forecasting.metrics import MAE, SMAPE, PoissonLoss, QuantileLoss
from pytorch_forecasting.models.temporal_fusion_transformer.tuning import optimize_hyperparameters

# TensorFlow/Keras
from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout
from keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping as ESLSTM

# Visualization libraries
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px

# Sklearn for preprocessing and metrics
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, root_mean_squared_error, r2_score

In [ ]:
import warnings

warnings.filterwarnings("ignore", category=UserWarning)  # Suppresses UserWarnings
warnings.filterwarnings("ignore", module="pytorch_forecasting")  # Suppresses warnings from PyTorch Forecasting

#### Load the preprocessed Apple stock dataset with sentiment analysis of Reddit and news data from Jan 2018 to Nov 2024

### **Note:** Before running the cell below, ensure that aapl_data_with_sentiment_analysis_from_18_to_24.csv file from the `Stock_Web_UI` folder is uploaded to the session storage.

In [ ]:
apple_fp = "/content/aapl_data_with_sentiment_analysis_from_18_to_24.csv"
# Load the dataset
apple_df = pd.read_csv(apple_fp)

#### Data Preprocesssing

In [ ]:
# Convert 'Date' to datetime format if it's not already
apple_df['Date'] = pd.to_datetime(apple_df['Date'])

# Set 'Date' as the index to enable resampling for missing dates
apple_df.set_index('Date', inplace=True)

# Resample to fill in missing dates, creating a continuous date range
apple_data = apple_df.resample('B').asfreq()  # 'B' for business days

# Fill missing values in numeric columns with interpolation
apple_df['Open'] = apple_df['Open'].interpolate(method='linear')
apple_df['High'] = apple_df['High'].interpolate(method='linear')
apple_df['Low'] = apple_df['Low'].interpolate(method='linear')
apple_df['Close'] = apple_df['Close'].interpolate(method='linear')
apple_df['Adj Close'] = apple_df['Adj Close'].interpolate(method='linear')
apple_df['Volume'] = apple_df['Volume'].interpolate(method='linear')

# Fill any remaining missing values with forward fill as a fallback
apple_df.fillna(method='ffill', inplace=True)

# Reset the index if you need 'Date' as a column again
apple_df.reset_index(inplace=True)

<ipython-input-51-a92d0cbc78e5>:19: FutureWarning:

DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.



In [ ]:
apple_df = apple_df.merge(
    apple_df[['Date']].drop_duplicates(ignore_index=True).rename_axis('time_idx').reset_index(),
    on='Date',
    how='left'
)

In [ ]:
apple_df

Date        Open        High         Low       Close   Adj Close  \
0    2018-01-02   42.540001   43.075001   42.314999   43.064999   40.524345   
1    2018-01-03   43.132500   43.637501   42.990002   43.057499   40.517288   
2    2018-01-04   43.134998   43.367500   43.020000   43.257500   40.705486   
3    2018-01-05   43.360001   43.842499   43.262501   43.750000   41.168930   
4    2018-01-08   43.587502   43.902500   43.482498   43.587502   41.016026   
...         ...         ...         ...         ...         ...         ...   
1735 2024-11-22  228.059998  230.720001  228.059998  229.869995  229.869995   
1736 2024-11-25  231.460007  233.250000  229.740005  232.869995  232.869995   
1737 2024-11-26  233.330002  235.570007  233.330002  235.059998  235.059998   
1738 2024-11-27  234.470001  235.690002  233.809998  234.929993  234.929993   
1739 2024-11-29  234.809998  237.809998  233.970001  237.330002  237.330002   

         Volume reddit_sentiment news_sentiment  time_idx  
0     102223600         Positive       Positive         0  
1     118071600          Neutral       Positive         1  
2      89738400          Neutral        Neutral         2  
3      94640000         Positive       Positive         3  
4      82271200         Positive       Positive         4  
...         ...              ...            ...       ...  
1735   38168300         Positive       Positive      1735  
1736   90152800          Neutral       Positive      1736  
1737   45986200          Neutral       Positive      1737  
1738   33498400          Neutral       Positive      1738  
1739   28481400          Neutral       Positive      1739  

[1740 rows x 10 columns]

### Define the dataset for the TFT model

In [ ]:
max_prediction_length = 30
min_encoder_length = 0
max_encoder_length = 180

apple_df['group_id'] = 0  # Assigning a constant group

# Define the TimeSeriesDataSet object
training_cutoff = apple_df['time_idx'].max() - max_prediction_length

In [ ]:
# Instantiate and fit encoders with add_nan=True to handle unknown categories
reddit_sentiment_encoder = NaNLabelEncoder(add_nan=True)
news_sentiment_encoder = NaNLabelEncoder(add_nan=True)

# Fit encoders on the relevant columns with NaN values filled
reddit_sentiment_encoder.fit(apple_df['reddit_sentiment'].fillna("Unknown"))
news_sentiment_encoder.fit(apple_df['news_sentiment'].fillna("Unknown"))

NaNLabelEncoder(add_nan=True, warn=True)

#### Create training set

In [ ]:
training = TimeSeriesDataSet(
    apple_df[lambda x: x.time_idx <= training_cutoff],
    time_idx="time_idx",
    target="Close", # target variable
    group_ids=["group_id"], # static covariates
    max_encoder_length=max_encoder_length, # maximum size of lookup window
    min_encoder_length=max_encoder_length//2,
    max_prediction_length=max_prediction_length, # maximum size of horizon window
    min_prediction_length=max_prediction_length,
    time_varying_known_categoricals=[],
    time_varying_known_reals=['Open', 'Volume'],
    time_varying_unknown_categoricals=['reddit_sentiment', 'news_sentiment'],
    time_varying_unknown_reals=['Close'],
    target_normalizer=GroupNormalizer(
        groups=["group_id"], transformation="softplus"
    ),  # use softplus transformation and normalize by group
    lags={'Close': [1,2,4,7,15,30,45,60]}, # add lagged values of target variable
    add_relative_time_idx=True,
    add_target_scales=True,
    add_encoder_length=True,
    categorical_encoders={
          # Properly handle unknown categories
        "reddit_sentiment": reddit_sentiment_encoder,
        "news_sentiment": news_sentiment_encoder
    }
)

In [ ]:
# create validation set
validation = TimeSeriesDataSet.from_dataset(training, apple_df, predict=True, stop_randomization=True)

# create dataloaders for model
batch_size = 128
train_dataloader = training.to_dataloader(train=True, batch_size=batch_size, num_workers=8)
val_dataloader = validation.to_dataloader(train=False, batch_size=batch_size * 10, num_workers=8)

In [ ]:
# calculate baseline mean absolute error
baseline_predictions = Baseline().predict(val_dataloader, return_y=True)
MAE()(baseline_predictions.output, baseline_predictions.y)

INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


tensor(4.5210, device='cuda:0')

### Defining the function to tune hyperparameters from Optuna

In [ ]:
import optuna
import lightning.pytorch as pl
from lightning.pytorch.callbacks import EarlyStopping, LearningRateMonitor
from pytorch_forecasting import TemporalFusionTransformer
from pytorch_forecasting.metrics import QuantileLoss, MAE
from pytorch_forecasting.data import GroupNormalizer

# Define the objective function for Optuna to tune hyperparameters
def objective(trial):
    # Suggest hyperparameters to tune
    learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-2)
    hidden_size = trial.suggest_int('hidden_size', 8, 64)
    attention_head_size = trial.suggest_int('attention_head_size', 1, 4)
    dropout = trial.suggest_uniform('dropout', 0.1, 0.5)

    # Define the TFT model with suggested hyperparameters
    tft = TemporalFusionTransformer.from_dataset(
        training,
        learning_rate=learning_rate,
        hidden_size=hidden_size,
        attention_head_size=attention_head_size,
        dropout=dropout,
        hidden_continuous_size=hidden_size // 2,  # Optional, adjusts continuous features
        loss=QuantileLoss(),
        optimizer="Adam"
    )

    # Set up the PyTorch Lightning Trainer with early stopping
    trainer = pl.Trainer(
        max_epochs=15,
        gradient_clip_val=0.1,
        callbacks=[EarlyStopping(monitor="val_loss", patience=5)],
        accelerator="gpu"
    )

    # Train the model
    trainer.fit(tft, train_dataloader, val_dataloader)

    # Get predictions on the validation set
    val_predictions = tft.predict(val_dataloader, return_y=True)

    # Calculate validation MAE as the optimization target
    val_mae = MAE()(val_predictions.output, val_predictions.y).item()
    return val_mae

# Run the hyperparameter optimization
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=30)  # Adjust n_trials for more exhaustive search if needed

# Print the best parameters found by Optuna
best_params = study.best_params
print("Best hyperparameters:", best_params)

[I 2024-12-03 14:07:36,049] A new study created in memory with name: no-name-e59fea74-5925-4f56-9e59-3d141e92b0cc
<ipython-input-60-917f4d71c040>:11: FutureWarning:

suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.

<ipython-input-60-917f4d71c040>:14: FutureWarning:

suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float instead.

INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVI

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO: `Trainer.fit` stopped: `max_epochs=15` reached.
INFO:lightning.pytorch.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=15` reached.
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
[I 2024-12-03 14:51:55,386] Trial 29 finished with value: 3.432547092437744 and parameters: {'learning_rate': 0.002168996375965692, 'hidden_size': 18, 'attention_head_size': 4, 'dropout': 0.41067595272066904}. Best is trial 10 with value: 1.8418971300125122.


Best hyperparameters: {'learning_rate': 0.00937239931655829, 'hidden_size': 10, 'attention_head_size': 3, 'dropout': 0.2492994960421437}


In [ ]:
best_params

{'learning_rate': 0.00937239931655829,
 'hidden_size': 10,
 'attention_head_size': 3,
 'dropout': 0.2492994960421437}

In [ ]:
# configure network and trainer
pl.seed_everything(42)
trainer = pl.Trainer(
    accelerator="gpu",
    gradient_clip_val=0.1,
)

tft = TemporalFusionTransformer.from_dataset(
    training,
    learning_rate=0.000760235330401722,
    hidden_size=41,
    attention_head_size=3,
    dropout=0.1383927412069838,
    hidden_continuous_size=22,
    loss=QuantileLoss(),
    optimizer="Adam"
)
print(f"Number of parameters in network: {tft.size()/1e3:.1f}k")

INFO: Seed set to 42
INFO:lightning.fabric.utilities.seed:Seed set to 42
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs


Number of parameters in network: 158.9k


#### Training the TFT model

In [ ]:
# Configure EarlyStopping with patience and monitoring validation loss
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=1e-4,
    patience=15,
    verbose=True,
    mode="min",
    stopping_threshold=None,
    check_finite=True
)

lr_logger = LearningRateMonitor()  # Log the learning rate
logger = TensorBoardLogger("lightning_logs")  # Log results to TensorBoard

trainer = pl.Trainer(
    accelerator="gpu",  # Set to "gpu" if you have a GPU available
    enable_model_summary=True,
    gradient_clip_val=0.1,
    limit_train_batches=1.0,  # Use the entire dataset for training
    callbacks=[lr_logger, early_stop_callback],
    logger=logger,
    check_val_every_n_epoch=1,  # Validate every epoch
)

# Define the Temporal Fusion Transformer
tft = TemporalFusionTransformer.from_dataset(
    training,
    learning_rate=0.000760235330401722,
    hidden_size=41,
    attention_head_size=3,
    dropout=0.1383927412069838,
    hidden_continuous_size=22,
    loss=QuantileLoss(),
    log_interval=10,
    optimizer="Adam",
    reduce_on_plateau_patience=4,
)

# Train the model
trainer.fit(tft, train_dataloader, val_dataloader)

INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: `Trainer(limit_train_batches=1.0)` was configured so 100% of the batches per epoch will be used..
INFO:lightning.pytorch.utilities.rank_zero:`Trainer(limit_train_batches=1.0)` was configured so 100% of the batches per epoch will be used..
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
   | Name                               | Type                            | Params | Mode 
------------------------------------------------------------------------------------------------
0  | loss                               | Quantile

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO: Metric val_loss improved. New best score: 23.410
INFO:lightning.pytorch.callbacks.early_stopping:Metric val_loss improved. New best score: 23.410


...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO: Monitored metric val_loss did not improve in the last 15 records. Best score: 1.099. Signaling Trainer to stop.
INFO:lightning.pytorch.callbacks.early_stopping:Monitored metric val_loss did not improve in the last 15 records. Best score: 1.099. Signaling Trainer to stop.


In [ ]:
# calcualte mean absolute error on validation set
predictions = tft.predict(val_dataloader, return_y=True, trainer_kwargs=dict(accelerator="cpu"))
MAE()(predictions.output, predictions.y)

INFO: GPU available: True (cuda), used: False
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: False
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs


tensor(2.0945)

#### Visualizations

In [ ]:
# Prepare Data for Visualization
actuals = predictions.y[0].detach().numpy().flatten()
preds = predictions.output.detach().numpy().flatten()

validation_dates = apple_df['Date'][-len(actuals):].values

# Calculate Mean Absolute Error (MAE)
mae = MAE()(predictions.output, predictions.y[0])
print(f"Mean Absolute Error: {mae.item()}")

# Create Plotly figure
fig = go.Figure()


fig.add_trace(go.Scatter(
    x=validation_dates,
    y=actuals,
    mode='lines',
    name='Actual Values',
    line=dict(color='blue')
))


fig.add_trace(go.Scatter(
    x=validation_dates,
    y=preds,
    mode='lines',
    name='Predicted Values',
    line=dict(color='green')
))

fig.update_layout(
    title="Predictions vs Actuals on Validation Set",
    xaxis_title="Date",
    yaxis_title="Stock Price",
    legend_title="Legend",
    template="plotly_dark"
)

# Show the plot
fig.show()

Mean Absolute Error: 2.094486951828003


In [ ]:
dates = apple_df['Date'][-len(actuals):].values

# Step 1: Create a DataFrame for Backtesting
trading_df = pd.DataFrame({
    'Date': dates,
    'Actual': actuals,
    'Predicted': preds
})
trading_df.set_index('Date', inplace=True)

# Calculate daily returns based on actual prices
trading_df['Daily Return'] = trading_df['Actual'].pct_change()

# Step 2: Generate Buy/Sell Signals Based on Predicted Prices
# Signal: 1 (Buy) if predicted price is higher than the previous prediction, -1 (Sell) otherwise
trading_df['Signal'] = np.where(trading_df['Predicted'].diff() > 0, 1, -1)

# Calculate strategy returns by shifting the signal by 1 to avoid lookahead bias
trading_df['Strategy Return'] = trading_df['Signal'].shift(1) * trading_df['Daily Return']

# Step 3: Calculate Cumulative Returns for Strategy and Benchmark
# Cumulative return for the TFT-based strategy
trading_df['Cumulative Strategy Return'] = (1 + trading_df['Strategy Return']).cumprod() - 1
# Cumulative return for a simple buy-and-hold strategy
trading_df['Cumulative Buy and Hold Return'] = (1 + trading_df['Daily Return']).cumprod() - 1

# Print final cumulative returns for both strategies
print(f"Final Strategy Return: {trading_df['Cumulative Strategy Return'].iloc[-1] * 100:.2f}%")
print(f"Final Buy and Hold Return: {trading_df['Cumulative Buy and Hold Return'].iloc[-1] * 100:.2f}%")

# Step 4: Plot Strategy vs. Buy-and-Hold Performance
fig = go.Figure()

# Cumulative strategy return plot
fig.add_trace(go.Scatter(
    x=trading_df.index,
    y=trading_df['Cumulative Strategy Return'],
    mode='lines',
    name='Cumulative Strategy Return',
    line=dict(color='blue')
))

# Cumulative buy-and-hold return plot
fig.add_trace(go.Scatter(
    x=trading_df.index,
    y=trading_df['Cumulative Buy and Hold Return'],
    mode='lines',
    name='Cumulative Buy and Hold Return',
    line=dict(color='green')
))

# Update layout for readability
fig.update_layout(
    title="TFT-Based Trading Strategy vs Buy-and-Hold",
    xaxis_title="Date",
    yaxis_title="Cumulative Return",
    template="plotly_dark"
)

fig.show()

Final Strategy Return: 2.02%
Final Buy and Hold Return: 0.99%


In [ ]:
# Set initial investment amount
initial_investment = 10000

# Calculate total earnings for the last 15 days
last_15_days = trading_df['Cumulative Strategy Return'].iloc[-15:]
final_return = last_15_days.iloc[-1]  # Get the last cumulative return

# Calculate final balance and earnings
final_balance = initial_investment * (1 + final_return)
earnings = final_balance - initial_investment

print(f"Initial Investment: ${initial_investment:,.2f}")
print(f"Final Balance after 15 days: ${final_balance:,.2f}")
print(f"Earnings over 15 days: ${earnings:,.2f}")

Initial Investment: $10,000.00
Final Balance after 15 days: $10,202.09
Earnings over 15 days: $202.09


#### Checking feature importance and MAE, RMSE, AND r2 Score for TFT Model

In [ ]:
# Calculate errors
errors = np.abs(actuals - preds)
fig = px.histogram(errors, nbins=50, title="Distribution of Absolute Errors", template="plotly_dark")
fig.update_layout(
    xaxis_title="Absolute Error",
    yaxis_title="Frequency"
)
fig.show()

# Print MAE and MSE
print(f"Mean Absolute Error: {mean_absolute_error(actuals, preds)}")
print(f"Mean Squared Error: {mean_squared_error(actuals, preds)}")

Mean Absolute Error: 2.094486951828003
Mean Squared Error: 7.430567741394043


In [ ]:
# Calculate RMSE and R²
rmse = root_mean_squared_error(actuals, preds)
r2 = r2_score(actuals, preds)

print(f"RMSE: {rmse}, R²: {r2}")

RMSE: 2.7259068489074707, R²: 0.6271860599517822


In [ ]:
# Using `mode="raw"` to get all outputs for interpretation
raw_predictions = tft.predict(val_dataloader, mode="raw", return_x=True)

# Unpack only what is necessary from raw_predictions
pred = raw_predictions[0]  # This contains the prediction values
x = raw_predictions[1]  # This contains input data used for interpretation

INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


In [ ]:
interpretation = tft.interpret_output(pred, reduction="mean")

In [ ]:
import pandas as pd
import plotly.express as px

# Extract feature importance from `static_variables`, `encoder_variables`, and `decoder_variables`
# Replace with actual feature names if needed
features = {
    "Static Features": interpretation["static_variables"].cpu().numpy(),
    "Encoder Features": interpretation["encoder_variables"].cpu().numpy(),
    "Decoder Features": interpretation["decoder_variables"].cpu().numpy(),
}

# Flatten the data for plotting
feature_names = []
feature_importance = []

for category, values in features.items():
    for i, value in enumerate(values):
        feature_names.append(f"{category}_{i+1}")  # or replace with actual feature names if available
        feature_importance.append(value)

# Create DataFrame for feature importance
importance_df = pd.DataFrame({
    "Feature": feature_names,
    "Importance": feature_importance
}).sort_values(by="Importance", ascending=False)

# Plot Feature Importance with Plotly
fig = px.bar(importance_df, x="Importance", y="Feature", orientation='h', title="Feature Importance", template="plotly_dark")
fig.update_layout(xaxis_title="Importance", yaxis_title="Feature")
fig.show()

In [ ]:
# Extract temporal attention values from the interpretation output
attention_weights = interpretation["attention"].cpu().numpy()  # Convert to numpy for easier handling
time_steps = list(range(len(attention_weights)))  # Generate time steps for x-axis

# Create the Plotly figure
fig = go.Figure()

# Plot attention weights as a single line
fig.add_trace(go.Scatter(
    x=time_steps,
    y=attention_weights,
    mode='lines',
    name="Attention Weight",
    line=dict(color='cyan')
))

# Update the layout for clarity
fig.update_layout(
    title="Temporal Attention Weights",
    xaxis_title="Time Steps",
    yaxis_title="Attention Weight",
    template="plotly_dark"
)

# Show the plot
fig.show()

### Downloading the Trained TFT Model of Apple stcok

In [ ]:
import torch
torch.save(tft.state_dict(), 'aapl_trained_tft_model.pth')
from google.colab import files
# Download the file
files.download('aapl_trained_tft_model.pth')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#### LSTM model

In [ ]:
# Load the dataset
apple_data = pd.read_csv(apple_fp)

# Parse dates and set the index
apple_data['Date'] = pd.to_datetime(apple_data['Date'])
apple_data.set_index('Date', inplace=True)

# Use only the 'Close' column for prediction
close_prices = apple_data[['Close']].values

# Scale the data to be between 0 and 1
scaler = MinMaxScaler(feature_range=(0, 1))
scaled_data = scaler.fit_transform(close_prices)

# Prepare the dataset for the LSTM
sequence_length = 90  # Using 90 days of historical data to predict the next day
X = []
y = []

for i in range(sequence_length, len(scaled_data)):
    X.append(scaled_data[i-sequence_length:i, 0])
    y.append(scaled_data[i, 0])

X, y = np.array(X), np.array(y)
X = np.reshape(X, (X.shape[0], X.shape[1], 1))  # Reshape for LSTM [samples, time steps, features]

# Split the data into training and testing sets
train_size = int(len(X) * 0.8)
X_train, X_test = X[:train_size], X[train_size:]
y_train, y_test = y[:train_size], y[train_size:]

# Build the LSTM model
model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], 1)))
model.add(Dropout(0.2))
model.add(LSTM(units=50, return_sequences=False))
model.add(Dropout(0.2))
model.add(Dense(units=25))
model.add(Dense(units=1))

# Compile the model
model.compile(optimizer=Adam(learning_rate=0.01), loss='mean_squared_error')

# Set up EarlyStopping callback
early_stopping = ESLSTM(
    monitor='val_loss',   # Monitor the validation loss
    patience=10,
    verbose=1,
    restore_best_weights=True
)

# Train the model with early stopping
history = model.fit(
    X_train, y_train,
    epochs=100,                # Set a high number of epochs
    batch_size=32,
    validation_data=(X_test, y_test),
    callbacks=[early_stopping], # Add the early stopping callback
    verbose=1
)

# Make predictions
lstm_predictions = model.predict(X_test)
predictions = scaler.inverse_transform(lstm_predictions)  # Invert scaling to get original values

# Invert scaling for y_test as well
y_test_scaled = scaler.inverse_transform(y_test.reshape(-1, 1))

Epoch 1/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 3s 18ms/step - loss: 0.0336 - val_loss: 9.2372e-04
Epoch 2/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0015 - val_loss: 0.0036
Epoch 3/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0011 - val_loss: 0.0011
Epoch 4/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0013 - val_loss: 8.8168e-04
Epoch 5/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0016 - val_loss: 0.0021
Epoch 6/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 9.1062e-04 - val_loss: 8.5136e-04
Epoch 7/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 8.3169e-04 - val_loss: 0.0053
Epoch 8/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0012 - val_loss: 0.0022
Epoch 9/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0012 - val_loss: 0.0021
Epoch 10/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 8.7780e-04 - val_loss: 0.0011
Epoch 11/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 8.3608e-04 - val_loss: 5.1502e-04
Epoch 12/100
42/42 ━

In [ ]:
# Calculate the Mean Absolute Error (MAE) between the actual and predicted values
mae_value = mean_absolute_error(y_test_scaled, lstm_predictions)
print(f"Mean Absolute Error (MAE): {mae_value}")

# Calculate the Mean Absolute Error (MAE) for the last 30 days
days = 30
mae_last_n_days = mean_absolute_error(y_test_scaled[-days:], predictions[-days:])
print(f"Mean Absolute Error (MAE) for the Last {days} Days: {mae_last_n_days}")

# Prepare the plot with Plotly for the last 30 days
fig = go.Figure()

# Only the last 30 days of actual prices and predictions
fig.add_trace(go.Scatter(x=apple_data.index[-len(y_test):][-days:], y=y_test_scaled.flatten()[-days:], mode='lines', name='Actual Prices'))
fig.add_trace(go.Scatter(x=apple_data.index[-len(y_test):][-days:], y=predictions.flatten()[-days:], mode='lines', name='Predicted Prices'))

# Update the layout
fig.update_layout(
    title="Last 30 Days Stock Price Prediction",
    xaxis_title="Date",
    yaxis_title="Stock Price",
    legend_title="Legend",
    template="plotly"
)

# Show the plot
fig.show()

Mean Absolute Error (MAE): 196.22078478643388
Mean Absolute Error (MAE) for the Last 30 Days: 3.083777364095054


In [ ]:
from sklearn.metrics import root_mean_squared_error, r2_score

# Calculate RMSE and R²
rmse = root_mean_squared_error(y_test_scaled, lstm_predictions)
r2 = r2_score(y_test_scaled, lstm_predictions)

print(f"RMSE: {rmse}, R²: {r2}")

RMSE: 197.4402584631038, R²: -79.40044291880513
